In [1]:
!git clone https://github.com/yl4579/StyleTTS-VC.git
%cd StyleTTS-VC

Cloning into 'StyleTTS-VC'...
remote: Enumerating objects: 85, done.
remote: Counting objects: 100% (33/33), done.
remote: Compressing objects: 100% (31/31), done.
remote: Total 85 (delta 12), reused 6 (delta 0), pack-reused 52
Unpacking objects: 100% (85/85), 102.59 MiB | 5.92 MiB/s, done.
Updating files: 100% (44/44), done.
/content/StyleTTS-VC


In [ ]:
!pip install SoundFile torchaudio munch torch pydub pyyaml librosa phonemizer attrdict git+https://github.com/resemble-ai/monotonic_align.git
!sudo apt-get install espeak-ng

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://github.com/resemble-ai/monotonic_align.git to /tmp/pip-req-build-_nmj3ai_
  Running command git clone --filter=blob:none --quiet https://github.com/resemble-ai/monotonic_align.git /tmp/pip-req-build-_nmj3ai_
  Resolved https://github.com/resemble-ai/monotonic_align.git to commit 78b985be210a03d08bc3acc01c4df0442105366f
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 90.6/90.6 kB 1.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 66.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.7/56.7 kB 7.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 162.6/162.6 kB 19.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 213.4/213.4 kB 24.5 MB

In [2]:
model_path = "https://drive.google.com/file/d/1bJbj3alOSu51riHUQl4G1GOjlzulyg6M/view?usp=sharing"
vocoder_path = "https://drive.google.com/file/d/1RDxYknrzncGzusYeVeDo38ErNdczzbik/view?usp=sharing"
ljspeech_sample_path = "https://drive.google.com/file/d/1aL8uAi-h6WlqDAbjauq5Cfs70gKmsHmb/view?usp=sharing"

In [3]:
import gdown
gdown.download(model_path, "Models_vc.zip", quiet=False, fuzzy=True)
gdown.download(vocoder_path, "Vocoder_vc.zip", quiet=False, fuzzy=True)
gdown.download(ljspeech_sample_path, "LJSpeech_sample.zip", quiet=False, fuzzy=True)

Downloading...
From: https://drive.google.com/uc?id=1bJbj3alOSu51riHUQl4G1GOjlzulyg6M
To: /content/StyleTTS-VC/Models_vc.zip
100%|██████████| 311M/311M [00:02<00:00, 130MB/s]
Downloading...
From: https://drive.google.com/uc?id=1RDxYknrzncGzusYeVeDo38ErNdczzbik
To: /content/StyleTTS-VC/Vocoder_vc.zip
100%|██████████| 53.2M/53.2M [00:00<00:00, 125MB/s]
Downloading...
From: https://drive.google.com/uc?id=1aL8uAi-h6WlqDAbjauq5Cfs70gKmsHmb
To: /content/StyleTTS-VC/LJSpeech_sample.zip
100%|██████████| 2.02M/2.02M [00:00<00:00, 148MB/s]


'LJSpeech_sample.zip'

In [4]:
!unzip -o /content/StyleTTS-VC/Models_vc.zip -d /content/StyleTTS-VC/
!unzip -o /content/StyleTTS-VC/Vocoder_vc.zip -d /content/StyleTTS-VC/
!unzip -o /content/StyleTTS-VC/LJSpeech_sample.zip -d /content/StyleTTS-VC/Data/
# Copy custom files to give style sample.
!cp -r /content/gdrive/MyDrive/voice/custom_sample /content/StyleTTS-VC/

Archive:  /content/StyleTTS-VC/Models_vc.zip
   creating: /content/StyleTTS-VC/Models/
   creating: /content/StyleTTS-VC/Models/VCTK/
  inflating: /content/StyleTTS-VC/Models/VCTK/config.yml  
  inflating: /content/StyleTTS-VC/Models/VCTK/epoch_2nd_00100.pth  
Archive:  /content/StyleTTS-VC/Vocoder_vc.zip
   creating: /content/StyleTTS-VC/Vocoder/
   creating: /content/StyleTTS-VC/Vocoder/LibriTTS/
  inflating: /content/StyleTTS-VC/Vocoder/LibriTTS/config.json  
  inflating: /content/StyleTTS-VC/Vocoder/LibriTTS/g_00935000  
   creating: /content/StyleTTS-VC/Vocoder/LibriTTS/.ipynb_checkpoints/
Archive:  /content/StyleTTS-VC/LJSpeech_sample.zip
   creating: /content/StyleTTS-VC/Data/LJSpeech-1.1/wavs/
  inflating: /content/StyleTTS-VC/Data/LJSpeech-1.1/wavs/LJ001-0001.wav  
  inflating: /content/StyleTTS-VC/Data/LJSpeech-1.1/wavs/LJ001-0002.wav  
  inflating: /content/StyleTTS-VC/Data/LJSpeech-1.1/wavs/LJ001-0003.wav  
  inflating: /content/StyleTTS-VC/Data/LJSpeech-1.1/wavs/LJ001-0004

In [ ]:
# load packages
import random
import yaml
from munch import Munch
import numpy as np
import torch
from torch import nn
import torch.nn.functional as F
import torchaudio
import librosa

from models import *
from utils import *

In [ ]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'

In [ ]:
device

'cuda'

In [ ]:
to_mel = torchaudio.transforms.MelSpectrogram(
    n_mels=80, n_fft=2048, win_length=1200, hop_length=300)
mean, std = -4, 4

def length_to_mask(lengths):
    mask = torch.arange(lengths.max()).unsqueeze(0).expand(lengths.shape[0], -1).type_as(lengths)
    mask = torch.gt(mask+1, lengths.unsqueeze(1))
    return mask

def preprocess(wave):
    wave_tensor = torch.from_numpy(wave).float()
    mel_tensor = to_mel(wave_tensor)
    mel_tensor = (torch.log(1e-5 + mel_tensor.unsqueeze(0)) - mean) / std
    return mel_tensor

def compute_style(ref_dicts):
    reference_embeddings = {}
    for key, path in ref_dicts.items():
        wave, sr = librosa.load(path, sr=24000)
        audio, index = librosa.effects.trim(wave, top_db=25)
        if sr != 24000:
            audio = librosa.resample(audio, sr, 24000)
        mel_tensor = preprocess(audio).to(device)

        with torch.no_grad():
            ref = model.style_encoder(mel_tensor.unsqueeze(1))
        reference_embeddings[key] = (ref.squeeze(1), audio)
    
    return reference_embeddings

In [ ]:
# load hifi-gan

import sys
sys.path.insert(0, "./Demo/hifi-gan")

import glob
import os
import argparse
import json
import torch
from scipy.io.wavfile import write
from attrdict import AttrDict
from vocoder import Generator
import librosa
import numpy as np
import torchaudio

h = None

def load_checkpoint(filepath, device):
    assert os.path.isfile(filepath)
    print("Loading '{}'".format(filepath))
    checkpoint_dict = torch.load(filepath, map_location=device)
    print("Complete.")
    return checkpoint_dict

def scan_checkpoint(cp_dir, prefix):
    pattern = os.path.join(cp_dir, prefix + '*')
    cp_list = glob.glob(pattern)
    if len(cp_list) == 0:
        return ''
    return sorted(cp_list)[-1]

cp_g = scan_checkpoint("Vocoder/LibriTTS/", 'g_')

config_file = os.path.join(os.path.split(cp_g)[0], 'config.json')
with open(config_file) as f:
    data = f.read()
json_config = json.loads(data)
h = AttrDict(json_config)

device = torch.device(device)
generator = Generator(h).to(device)

state_dict_g = load_checkpoint(cp_g, device)
generator.load_state_dict(state_dict_g['generator'])
generator.eval()
generator.remove_weight_norm()

Loading 'Vocoder/LibriTTS/g_00935000'
Complete.
Removing weight norm...


In [ ]:
# load StyleTTS
model_path = "./Models/VCTK/epoch_2nd_00100.pth"
model_config_path = "./Models/VCTK/config.yml"

config = yaml.safe_load(open(model_config_path))

# load pretrained ASR model
ASR_config = config.get('ASR_config', False)
ASR_path = config.get('ASR_path', False)
text_aligner = load_ASR_models(ASR_path, ASR_config)

# load pretrained F0 model
F0_path = config.get('F0_path', False)
pitch_extractor = load_F0_models(F0_path)

model = build_model(Munch(config['model_params']), text_aligner, pitch_extractor)

params = torch.load(model_path, map_location='cpu')
params = params['net']
for key in model:
    if key in params:
        if not "discriminator" in key:
            print('%s loaded' % key)
            model[key].load_state_dict(params[key])
_ = [model[key].eval() for key in model]
_ = [model[key].to(device) for key in model]

mel_encoder loaded
linear_proj loaded
decoder loaded
pitch_extractor loaded
text_encoder loaded
style_encoder loaded
text_aligner loaded


In [ ]:
# # get first 3 validation sample as references

# train_path = config.get('train_data', None)
# val_path = config.get('val_data', None)
# train_list, val_list = get_data_path_list(train_path, val_path)

# ref_dicts = {}
# for j in range(3):
#     filename = val_list[j].split('|')[0]
#     name = filename.split('/')[-1].replace('.wav', '')
#     ref_dicts[name] = filename

# Manually refer to data
ref_dicts = {
    "LJ001-0001" : "/content/StyleTTS-VC/Data/LJSpeech-1.1/wavs/LJ001-0001.wav",
    "LJ001-0002" : "/content/StyleTTS-VC/Data/LJSpeech-1.1/wavs/LJ001-0002.wav",
    "LJ001-0003" : "/content/StyleTTS-VC/Data/LJSpeech-1.1/wavs/LJ001-0003.wav",
    "LJ001-0004" :"/content/StyleTTS-VC/Data/LJSpeech-1.1/wavs/LJ001-0004.wav",
    "LJ001-0005" : "/content/StyleTTS-VC/Data/LJSpeech-1.1/wavs/LJ001-0005.wav",
}

reference_embeddings = compute_style(ref_dicts)

In [ ]:
# get last validation sample as input
filename = "/content/StyleTTS-VC/custom_sample/wavs/10_569880_577880.wav"
audio, source_sr = librosa.load(filename, sr=24000)
audio, index = librosa.effects.trim(audio, top_db=30)
audio = audio / np.max(np.abs(audio))
audio.dtype = np.float32
source = preprocess(audio).to(device)

In [ ]:


converted_samples = {}

with torch.no_grad():
    mel_input_length = torch.LongTensor([source.shape[-1]])
    asr = model.mel_encoder(source)
    F0_real, _, F0 = model.pitch_extractor(source.unsqueeze(1))
    real_norm = log_norm(source.unsqueeze(1)).squeeze(1)
    
    for key, (ref, _) in reference_embeddings.items():
        out = model.decoder(asr, F0_real.unsqueeze(0), real_norm, ref.squeeze(1))

        c = out.squeeze()
        y_g_hat = generator(c.unsqueeze(0))
        y_out = y_g_hat.squeeze()

        converted_samples[key] = y_out.cpu().numpy()



In [ ]:


import IPython.display as ipd
for key, wave in converted_samples.items():
    print('Converted: %s' % key)
    display(ipd.Audio(wave, rate=24000))
    try:
        print('Reference: %s' % key)
        display(ipd.Audio(reference_embeddings[key][-1], rate=24000))
    except:
        continue

print('Original:')
display(ipd.Audio(audio, rate=24000))



Converted: LJ001-0001


Reference: LJ001-0001


Converted: LJ001-0002


Reference: LJ001-0002


Converted: LJ001-0003


...

Converted: LJ001-0004


Reference: LJ001-0004


Converted: LJ001-0005


Reference: LJ001-0005


Original:
